In [554]:
import pandas as pd
import pandas_profiling
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
from sklearn.decomposition import PCA, TruncatedSVD
from sklearn.cluster import KMeans, DBSCAN
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import pairwise_distances
import plotly.express as px
from sklearn.mixture import GaussianMixture
from sklearn.metrics import silhouette_score as ss


import joblib
import warnings
warnings.filterwarnings(action='ignore') 
seed = 43

# Train
## Data Load -> Scailing -> SVD -> DBSCAN -> get Best EPS, Min_samples

In [555]:
train_df = pd.read_csv("./dataset/train_data.csv")


In [556]:
# train_df.profile_report()

In [557]:
features = train_df.columns[:-1]
features

Index(['air_inflow', 'air_end_temp', 'out_pressure', 'motor_current',
       'motor_rpm', 'motor_temp', 'motor_vibe'],
      dtype='object')

In [558]:
X_train = train_df[features]
y_train = train_df[['type']]


In [559]:
sc = StandardScaler()
X_train[features]= sc.fit_transform(X_train)
X_train.head(2)

air_inflow  air_end_temp  out_pressure  motor_current  motor_rpm  \
0   -0.448257     -0.917212 -1.110223e-16      -0.511748  -1.007046   
1    0.699749      1.178320 -1.110223e-16       0.802045   1.118785   

   motor_temp  motor_vibe  
0   -0.910351   -0.331821  
1    1.172883    0.188462

In [560]:
train_df = X_train
train_df['type'] = y_train
train_df.head(2)

air_inflow  air_end_temp  out_pressure  motor_current  motor_rpm  \
0   -0.448257     -0.917212 -1.110223e-16      -0.511748  -1.007046   
1    0.699749      1.178320 -1.110223e-16       0.802045   1.118785   

   motor_temp  motor_vibe  type  
0   -0.910351   -0.331821     0  
1    1.172883    0.188462     0

In [561]:
# train_df.profile_report()

In [562]:
g1 = ['air_inflow','motor_current']
g2 = ['air_end_temp', 'motor_rpm', 'motor_temp']
g3 = ['motor_vibe', 'out_pressure']

g1_train = train_df[g1]
g2_train = train_df[g2]
g3_train = train_df[g3]
y_train = train_df[['type']]
combined_train = [g1_train, g2_train, g3_train]

svd= TruncatedSVD(n_components=1, n_iter=10, random_state=seed)
svd_list = []
for i in combined_train:
    result = svd.fit_transform(i)
    svd_list.append(result)
    total_var = svd.explained_variance_ratio_.sum() * 100
    print(f"{i}explained_variance_ratio : {total_var}")
    
flat_svd_list = []
for i in svd_list:
    result = [j for sub in i for j in sub]
    flat_svd_list.append(result)
svd_train_df = pd.DataFrame({"PC1": flat_svd_list[0], "PC2": flat_svd_list[1], "PC3": flat_svd_list[2]})
svd_train_df = pd.concat([svd_train_df, y_train], axis=1)
svd_train_df.info()

      air_inflow  motor_current
0      -0.448257      -0.511748
1       0.699749       0.802045
2      -0.182053      -0.202966
3       0.200616       0.230799
4      -0.190372      -0.208848
...          ...            ...
2458    0.125746       0.149927
2459   -0.073907      -0.084600
2460   -0.781013      -0.889638
2461   -0.764375      -0.871259
2462    0.491777       0.566048

[2463 rows x 2 columns]explained_variance_ratio : 99.72924966859078
      air_end_temp  motor_rpm  motor_temp
0        -0.917212  -1.007046   -0.910351
1         1.178320   1.118785    1.172883
2        -0.425427  -0.508305   -0.421612
3         0.266970   0.194005    0.265958
4        -0.434598  -0.517029   -0.430592
...            ...        ...         ...
2458      0.137432   0.063140    0.137680
2459     -0.236279  -0.316369   -0.234326
2460     -1.520194  -1.619204   -1.510693
2461     -1.490389  -1.588669   -1.481189
2462      0.801170   0.736368    0.798312

[2463 rows x 3 columns]explained_variance_

In [563]:
# svd= TruncatedSVD(n_components=3, n_iter=10, random_state=seed)
# svd_train_df = svd.fit_transform(X_train)
# svd_train_df = pd.DataFrame({"PC1": svd_train_df.T[0], "PC2": svd_train_df.T[1], "PC3": svd_train_df.T[2]})
# svd_train_df = pd.concat([svd_train_df, y_train], axis=1)
# svd_train_df

In [564]:
tdf0_train = svd_train_df[svd_train_df.type == 0]
tdf1_train = svd_train_df[svd_train_df.type == 1]
tdf2_train = svd_train_df[svd_train_df.type == 2]
tdf3_train = svd_train_df[svd_train_df.type == 3]
tdf4_train = svd_train_df[svd_train_df.type == 4]
tdf5_train = svd_train_df[svd_train_df.type == 5]
tdf6_train = svd_train_df[svd_train_df.type == 6]
tdf7_train = svd_train_df[svd_train_df.type == 7]
tdf_train = [tdf0_train, tdf1_train, tdf2_train, tdf3_train, tdf4_train, tdf5_train, tdf6_train, tdf7_train]

In [565]:
def draw_chart_type(df):
    title = f"type {str(df.type.unique()[0])}"
    fig = px.scatter_3d(
        df, x='PC1', y='PC2', z='PC3', color='type',symbol='type', opacity=0.5, size_max=10,height=800,title=title,
    )
    fig.show()

In [566]:
# for tdf in tdf_train:
#     draw_chart_type(tdf)

In [567]:
epsilons = np.linspace(0.1, 2, num=50)
epsilons

array([0.1       , 0.13877551, 0.17755102, 0.21632653, 0.25510204,
       0.29387755, 0.33265306, 0.37142857, 0.41020408, 0.44897959,
       0.4877551 , 0.52653061, 0.56530612, 0.60408163, 0.64285714,
       0.68163265, 0.72040816, 0.75918367, 0.79795918, 0.83673469,
       0.8755102 , 0.91428571, 0.95306122, 0.99183673, 1.03061224,
       1.06938776, 1.10816327, 1.14693878, 1.18571429, 1.2244898 ,
       1.26326531, 1.30204082, 1.34081633, 1.37959184, 1.41836735,
       1.45714286, 1.49591837, 1.53469388, 1.57346939, 1.6122449 ,
       1.65102041, 1.68979592, 1.72857143, 1.76734694, 1.80612245,
       1.84489796, 1.88367347, 1.92244898, 1.96122449, 2.        ])

In [568]:
min_samples = np.arange(2, 20, step=1)
min_samples

array([ 2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17, 18,
       19])

In [569]:
epsilons = epsilons
min_samples = min_samples
import itertools
combinations = list(itertools.product(epsilons, min_samples))
N = len(combinations)
N

900

In [570]:
def get_scores_and_labels(combinations, X):
  scores = []
  all_labels_list = []

  for i, (eps, num_samples) in enumerate(combinations):
    dbscan_cluster_model = DBSCAN(eps=eps, min_samples=num_samples).fit(X)
    labels = dbscan_cluster_model.labels_
    labels_set = set(labels)
    num_clusters = len(labels_set)
    if -1 in labels_set:
      num_clusters -= 1
    
    if (num_clusters < 2) or (num_clusters > 50):
      scores.append(-10)
      all_labels_list.append('bad')
      c = (eps, num_samples)
      print(f"Combination {c} on iteration {i+1} of {N} has {num_clusters} clusters. Moving on")
      continue
    try:
        scores.append(ss(X, labels))
        all_labels_list.append(labels)
        print(f"Index: {i}, Score: {scores[-1]}, Labels: {all_labels_list[-1]}, NumClusters: {num_clusters}")
    except:
        scores.append('ss Failure')

  best_index = np.argmax(scores)
  best_parameters = combinations[best_index]
  best_labels = all_labels_list[best_index]
  best_score = scores[best_index]

  return {'best_epsilon': best_parameters[0],
          'best_min_samples': best_parameters[1], 
          'best_labels': best_labels,
          'best_score': best_score}

In [571]:
best_hyperparams = []

for tdf in tdf_train:
    X_train = tdf.iloc[:,:-1]
    y_train = tdf[['type']]
    
    hyperparam = get_scores_and_labels(combinations, tdf)
    best_hyperparams.append(hyperparam)
    
    tdf['cluster'] = hyperparam['best_labels']
    print("="*70)   

Combination (0.1, 2) on iteration 1 of 900 has 1 clusters. Moving on
Combination (0.1, 3) on iteration 2 of 900 has 1 clusters. Moving on
Combination (0.1, 4) on iteration 3 of 900 has 1 clusters. Moving on
Combination (0.1, 5) on iteration 4 of 900 has 1 clusters. Moving on
Combination (0.1, 6) on iteration 5 of 900 has 1 clusters. Moving on
Combination (0.1, 7) on iteration 6 of 900 has 1 clusters. Moving on
Index: 6, Score: 0.1950506940354143, Labels: [ 0  1  0  0  0  0  1  1  0  1 -1  0  0  1  1  1  0  0  1  0  0  0  1  1
  0  1  0  1  0  0  0  1  1  0  0  1  0  0  0  0  1  0  0  0  0  1  0  1
  0  0  0  1  0  1  0  1  1  0  1  0  0  1  0  0  1  0  0  0  0  0  0  0
  1  0  1  0  1  0  1  0  1  0  0  1  0  1  1  0  1  0  0  1  0  1  0  0
  0  1  1  1  0  1  1  0  1  0  0  1  1  0  0  1  1  1  1  0  0  1  1  0
  0  0  0  1  0  1  0  0 -1  0  1  1  0  1  0  0  1  0  1  0  0  1  0  1
  0 -1  0  0  0  1  0  1  1  0  0  0  1  0  1  0  1  1  1  1  0  0  0  1
  0  0  1  0  0  0  0  0  0  1

Index: 14, Score: 0.234173484217164, Labels: [11 -1 -1 10 -1 -1  2  0  1  2 -1 -1 10  3 12 -1  4 -1  3  4 -1  5  2  3
  6 12  6  3 11  4  5 -1 -1 11  5  0 -1 -1  1 10  9  6  1  8  5  0 11  9
 -1 -1 -1 -1  8  0  4  2 -1 11  2 -1  4  9  6  6  3  8  7 -1  5 -1 -1  7
  3 -1  0 -1 -1  4  2  6  3  1  1  0  5 -1  0 -1 -1 -1  8  3  7  9 -1 -1
  7  9 -1  0 -1  3  3 -1 -1  5  8  2  3 -1 -1  0  3  3  0  1  8  2  2  1
 -1 -1  5 -1 -1 -1  4  7 -1 -1  3  0 -1  3 -1 10  3  8 -1  5  1  9 -1  2
  5 -1  5  5 -1 -1  4  0  9  5 -1  5  9  4  9  1  2  9  3  0 -1  1  1 12
  1  1  3  1  6 -1 -1 -1  1  0 -1 -1  7 -1  7 11 -1  3  0  1 10 -1  5  3
  7 -1  7  9  7 10  0  3  1  3 11 -1  2 -1 -1  1  0  3  1  8 -1  8  0 -1
 11 -1 10  4 11 -1  6  6 -1  6  5  6  4  8  3  1  6  7 12  0  3  1 12 10
 -1 -1 11 11 -1 10 12  0 -1  5 11  4  2  3 -1  0 -1 -1  7 -1 -1 -1 11 -1
 10  0  8  2  5 -1  8  2  8 -1 -1 11  3  0  6 -1 -1 -1  3  2 -1  3 10  2
  3 10  2 -1 -1  5  2 -1 -1  0  2 12 11  3  1  3 -1  4  4  2 -1  4  2 -1
  6  6

Index: 35, Score: 0.37635147298884924, Labels: [ 0  2 -1  8 -1  1  2  3  1  2 -1  9  8  4  5  2  7  9  4  7  1  6  2  4
  0  5  0  4  0  7  6  5  4  0  6  3  0 -1  1  8  3  0  1  9  6  3  0  3
 -1 -1 -1  5  9  3  7  2  2  0  2  1  7  3  0  0  4  9  1  9  6 -1 -1  1
  4  7  3 -1  3  7  2  0  4  1  1  3  6  2  3 -1 -1  9 -1  4  1  5 -1 -1
  1  5  2  3 -1  4  4 -1  2  6 -1  2  4  1 -1  3  4  4  3  1 -1  2  2  1
  6  0  6  3  0  3  7  1 -1  0  4  3 -1  4  6  8  4 -1  2  6  1  3  1  2
  6 -1  6  6 -1  5  7  3  5  6 -1  6  5  7  5  1  2  3  4  3  0  1  1  5
  1  1  4  1  0  9 -1 -1  1  3 -1  5  1  5  1  0 -1  4  3  1  8  9  6  4
  1  2  1  3  1  8  3  4  1  4  0  0  2  9  2  1  3  4  1 -1  1 -1  3  4
  0 -1  8  7  0  1  0  0  1  0  6  0  7 -1  4  1  0  1  5  3  4  1  5  8
  4  4  0  0  8  8  5  3 -1  6  0  7  2  4  7  3  0  5  1  4 -1  0  0  1
  8  3 -1  2  6  2  9  2  9  2  2  0  4  3  0  0  1  2  4  2 -1  4  8  2
  4  8  2  1  2  6  2  2  5  3  2  5  0  4  1  4  3  7  7  2  9  7  2  1
  0 

Combination (0.3326530612244898, 10) on iteration 117 of 900 has 1 clusters. Moving on
Combination (0.3326530612244898, 11) on iteration 118 of 900 has 1 clusters. Moving on
Combination (0.3326530612244898, 12) on iteration 119 of 900 has 1 clusters. Moving on
Combination (0.3326530612244898, 13) on iteration 120 of 900 has 1 clusters. Moving on
Combination (0.3326530612244898, 14) on iteration 121 of 900 has 1 clusters. Moving on
Combination (0.3326530612244898, 15) on iteration 122 of 900 has 1 clusters. Moving on
Combination (0.3326530612244898, 16) on iteration 123 of 900 has 1 clusters. Moving on
Combination (0.3326530612244898, 17) on iteration 124 of 900 has 1 clusters. Moving on
Combination (0.3326530612244898, 18) on iteration 125 of 900 has 1 clusters. Moving on
Combination (0.3326530612244898, 19) on iteration 126 of 900 has 1 clusters. Moving on
Combination (0.37142857142857144, 2) on iteration 127 of 900 has 1 clusters. Moving on
Combination (0.37142857142857144, 3) on ite

Combination (0.5265306122448979, 18) on iteration 215 of 900 has 1 clusters. Moving on
Combination (0.5265306122448979, 19) on iteration 216 of 900 has 1 clusters. Moving on
Combination (0.5653061224489796, 2) on iteration 217 of 900 has 1 clusters. Moving on
Combination (0.5653061224489796, 3) on iteration 218 of 900 has 1 clusters. Moving on
Combination (0.5653061224489796, 4) on iteration 219 of 900 has 1 clusters. Moving on
Combination (0.5653061224489796, 5) on iteration 220 of 900 has 1 clusters. Moving on
Combination (0.5653061224489796, 6) on iteration 221 of 900 has 1 clusters. Moving on
Combination (0.5653061224489796, 7) on iteration 222 of 900 has 1 clusters. Moving on
Combination (0.5653061224489796, 8) on iteration 223 of 900 has 1 clusters. Moving on
Combination (0.5653061224489796, 9) on iteration 224 of 900 has 1 clusters. Moving on
Combination (0.5653061224489796, 10) on iteration 225 of 900 has 1 clusters. Moving on
Combination (0.5653061224489796, 11) on iteration 2

...

Combination (1.1081632653061226, 17) on iteration 484 of 900 has 1 clusters. Moving on
Combination (1.1081632653061226, 18) on iteration 485 of 900 has 1 clusters. Moving on
Combination (1.1081632653061226, 19) on iteration 486 of 900 has 1 clusters. Moving on
Combination (1.146938775510204, 2) on iteration 487 of 900 has 1 clusters. Moving on
Combination (1.146938775510204, 3) on iteration 488 of 900 has 1 clusters. Moving on
Combination (1.146938775510204, 4) on iteration 489 of 900 has 1 clusters. Moving on
Combination (1.146938775510204, 5) on iteration 490 of 900 has 1 clusters. Moving on
Combination (1.146938775510204, 6) on iteration 491 of 900 has 1 clusters. Moving on
Combination (1.146938775510204, 7) on iteration 492 of 900 has 1 clusters. Moving on
Combination (1.146938775510204, 8) on iteration 493 of 900 has 1 clusters. Moving on
Combination (1.146938775510204, 9) on iteration 494 of 900 has 1 clusters. Moving on
Combination (1.146938775510204, 10) on iteration 495 of 900

Combination (1.3408163265306123, 17) on iteration 592 of 900 has 1 clusters. Moving on
Combination (1.3408163265306123, 18) on iteration 593 of 900 has 1 clusters. Moving on
Combination (1.3408163265306123, 19) on iteration 594 of 900 has 1 clusters. Moving on
Combination (1.379591836734694, 2) on iteration 595 of 900 has 1 clusters. Moving on
Combination (1.379591836734694, 3) on iteration 596 of 900 has 1 clusters. Moving on
Combination (1.379591836734694, 4) on iteration 597 of 900 has 1 clusters. Moving on
Combination (1.379591836734694, 5) on iteration 598 of 900 has 1 clusters. Moving on
Combination (1.379591836734694, 6) on iteration 599 of 900 has 1 clusters. Moving on
Combination (1.379591836734694, 7) on iteration 600 of 900 has 1 clusters. Moving on
Combination (1.379591836734694, 8) on iteration 601 of 900 has 1 clusters. Moving on
Combination (1.379591836734694, 9) on iteration 602 of 900 has 1 clusters. Moving on
Combination (1.379591836734694, 10) on iteration 603 of 900

Combination (1.573469387755102, 5) on iteration 688 of 900 has 1 clusters. Moving on
Combination (1.573469387755102, 6) on iteration 689 of 900 has 1 clusters. Moving on
Combination (1.573469387755102, 7) on iteration 690 of 900 has 1 clusters. Moving on
Combination (1.573469387755102, 8) on iteration 691 of 900 has 1 clusters. Moving on
Combination (1.573469387755102, 9) on iteration 692 of 900 has 1 clusters. Moving on
Combination (1.573469387755102, 10) on iteration 693 of 900 has 1 clusters. Moving on
Combination (1.573469387755102, 11) on iteration 694 of 900 has 1 clusters. Moving on
Combination (1.573469387755102, 12) on iteration 695 of 900 has 1 clusters. Moving on
Combination (1.573469387755102, 13) on iteration 696 of 900 has 1 clusters. Moving on
Combination (1.573469387755102, 14) on iteration 697 of 900 has 1 clusters. Moving on
Combination (1.573469387755102, 15) on iteration 698 of 900 has 1 clusters. Moving on
Combination (1.573469387755102, 16) on iteration 699 of 900

Combination (1.806122448979592, 6) on iteration 797 of 900 has 1 clusters. Moving on
Combination (1.806122448979592, 7) on iteration 798 of 900 has 1 clusters. Moving on
Combination (1.806122448979592, 8) on iteration 799 of 900 has 1 clusters. Moving on
Combination (1.806122448979592, 9) on iteration 800 of 900 has 1 clusters. Moving on
Combination (1.806122448979592, 10) on iteration 801 of 900 has 1 clusters. Moving on
Combination (1.806122448979592, 11) on iteration 802 of 900 has 1 clusters. Moving on
Combination (1.806122448979592, 12) on iteration 803 of 900 has 1 clusters. Moving on
Combination (1.806122448979592, 13) on iteration 804 of 900 has 1 clusters. Moving on
Combination (1.806122448979592, 14) on iteration 805 of 900 has 1 clusters. Moving on
Combination (1.806122448979592, 15) on iteration 806 of 900 has 1 clusters. Moving on
Combination (1.806122448979592, 16) on iteration 807 of 900 has 1 clusters. Moving on
Combination (1.806122448979592, 17) on iteration 808 of 90

Combination (2.0, 16) on iteration 897 of 900 has 1 clusters. Moving on
Combination (2.0, 17) on iteration 898 of 900 has 1 clusters. Moving on
Combination (2.0, 18) on iteration 899 of 900 has 1 clusters. Moving on
Combination (2.0, 19) on iteration 900 of 900 has 1 clusters. Moving on


In [572]:
best_hyperparams[0]

{'best_epsilon': 0.13877551020408163,
 'best_min_samples': 13,
 'best_labels': array([0, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0,
        1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0,
        0, 1, 0, 1, 0, 0, 0, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 1, 1, 0,
        0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0,
        0, 1, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1,
        0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 1, 0,
        0, 0, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0,
        1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1, 0, 0, 0,
        0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0,
        0, 1, 0, 1, 0, 1, 0, 1, 0,

In [573]:
best_eps = [best_hyperparams[i]['best_epsilon'] for i in range(8)]
best_eps

[0.13877551020408163,
 0.8755102040816326,
 0.1,
 0.17755102040816328,
 0.13877551020408163,
 0.17755102040816328,
 0.13877551020408163,
 0.17755102040816328]

In [574]:
best_min_samples = [best_hyperparams[i]['best_min_samples'] for i in range(8)]
best_min_samples

[13, 2, 2, 10, 8, 2, 2, 2]

In [575]:
best_sil_score = [best_hyperparams[i]['best_score'] for i in range(8)]
best_sil_score

[0.5277549447571676,
 0.8260353154883753,
 0.5716122215843363,
 0.5613954395524381,
 0.6372519605569298,
 0.6244164542412234,
 0.6120270877318422,
 0.6539291521493604]

In [576]:
best_labels = best_hyperparams[0]['best_labels'].tolist()+best_hyperparams[1]['best_labels'].tolist()+best_hyperparams[2]['best_labels'].tolist()+best_hyperparams[3]['best_labels'].tolist()+best_hyperparams[4]['best_labels'].tolist()+best_hyperparams[5]['best_labels'].tolist()+best_hyperparams[6]['best_labels'].tolist()+best_hyperparams[7]['best_labels'].tolist()
len(best_labels)

2463

In [577]:
svd_train_df['label'] = best_labels

In [578]:
svd_train_df.head(3)

PC1       PC2       PC3  type  label
0 -0.678826  1.636428 -0.331821     0      0
1  1.061929 -2.003479  0.188462     0      1
2 -0.272250  0.782386 -0.211268     0      0

In [579]:
tdf0_train = svd_train_df[svd_train_df.type == 0]
tdf1_train = svd_train_df[svd_train_df.type == 1]
tdf2_train = svd_train_df[svd_train_df.type == 2]
tdf3_train = svd_train_df[svd_train_df.type == 3]
tdf4_train = svd_train_df[svd_train_df.type == 4]
tdf5_train = svd_train_df[svd_train_df.type == 5]
tdf6_train = svd_train_df[svd_train_df.type == 6]
tdf7_train = svd_train_df[svd_train_df.type == 7]
tdf_train = [tdf0_train, tdf1_train, tdf2_train, tdf3_train, tdf4_train, tdf5_train, tdf6_train, tdf7_train]

In [580]:
def draw_chart_label(df):
    title = f"type {str(df.type.unique()[0])}"
    fig = px.scatter_3d(
        df, x='PC1', y='PC2', z='PC3', color='label',symbol='type', opacity=0.5, size_max=10,height=800,title=title,
    )
    fig.show()

In [581]:
# for tdf in tdf_train:
#     draw_chart_label(tdf)

In [582]:
X = svd_train_df.iloc[:,:-1]
gm = GaussianMixture(n_components=20, covariance_type='spherical', random_state=seed).fit(X)
gm_labels = gm.predict(X)
gm_proba = gm.predict_proba(X)
gm_new_probas = []
for i in gm_proba:
    k = np.around(i.astype(np.double), 6)
    gm_new_probas.append(k)
gm_new_probas

[array([0.      , 0.      , 0.      , 0.019187, 0.      , 0.      ,
        0.      , 0.980813, 0.      , 0.      , 0.      , 0.      ,
        0.      , 0.      , 0.      , 0.      , 0.      , 0.      ,
        0.      , 0.      ]),
 array([0.00000e+00, 8.00000e-06, 0.00000e+00, 0.00000e+00, 0.00000e+00,
        0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00, 9.99989e-01,
        0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00,
        0.00000e+00, 0.00000e+00, 3.00000e-06, 0.00000e+00, 0.00000e+00]),
 array([0.00000e+00, 0.00000e+00, 0.00000e+00, 9.99123e-01, 0.00000e+00,
        0.00000e+00, 0.00000e+00, 8.77000e-04, 0.00000e+00, 0.00000e+00,
        0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00,
        0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00]),
 array([0.00000e+00, 2.58400e-03, 0.00000e+00, 9.97414e-01, 0.00000e+00,
        0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00,
        0.00000e+00, 0.00000e+00

In [583]:
svd_train_df['gm_label'] = gm_labels
svd_train_df['gm_proba'] = gm_new_probas
svd_train_df['gm_label'].value_counts()

3     266
7     229
2     153
12    151
8     143
11    142
0     142
10    141
15    135
13    126
14    125
9     108
17    104
18     98
4      85
19     83
1      78
6      70
16     68
5      16
Name: gm_label, dtype: int64

In [584]:
svd_train_df.head()

PC1       PC2       PC3  type  label  gm_label  \
0 -0.678826  1.636428 -0.331821     0      0         7   
1  1.061929 -2.003479  0.188462     0      1         9   
2 -0.272250  0.782386 -0.211268     0      0         3   
3  0.305056 -0.419799 -0.039955     0      0         3   
4 -0.282291  0.797902 -0.211268     0      0         3   

                                            gm_proba  
0  [0.0, 0.0, 0.0, 0.019187, 0.0, 0.0, 0.0, 0.980...  
1  [0.0, 8e-06, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0...  
2  [0.0, 0.0, 0.0, 0.999123, 0.0, 0.0, 0.0, 0.000...  
3  [0.0, 0.002584, 0.0, 0.997414, 0.0, 0.0, 0.0, ...  
4  [0.0, 0.0, 0.0, 0.998912, 0.0, 0.0, 0.0, 0.001...

In [585]:
train_result = svd_train_df.groupby(['type', 'gm_label'])['gm_proba'].count().reset_index()
train_result.to_csv('train1.csv', encoding="utf-8-sig")

# Test
## Data Load -> Scailing -> SVD -> DBSCAN(with Best EPS, Min_samples) -> Get Label

In [586]:
test_df = pd.read_csv("./dataset/test_data.csv")
X_test = test_df[features]
y_test = test_df[['type']]

In [587]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7389 entries, 0 to 7388
Data columns (total 8 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   air_inflow     7389 non-null   float64
 1   air_end_temp   7389 non-null   float64
 2   out_pressure   7389 non-null   float64
 3   motor_current  7389 non-null   float64
 4   motor_rpm      7389 non-null   int64  
 5   motor_temp     7389 non-null   float64
 6   motor_vibe     7389 non-null   float64
 7   type           7389 non-null   int64  
dtypes: float64(6), int64(2)
memory usage: 461.9 KB


In [588]:
sc = StandardScaler()
X_test[features]= sc.fit_transform(X_test)
X_test.head(2)

air_inflow  air_end_temp  out_pressure  motor_current  motor_rpm  \
0    0.349570      0.487848      0.029701       0.387062   0.419055   
1    0.478445      0.713509      0.029701       0.531396   0.647355   

   motor_temp  motor_vibe  
0    0.491978    0.208765  
1    0.716757    0.348482

In [589]:
test_df = X_test
test_df['type'] = y_test
test_df.head(2)

air_inflow  air_end_temp  out_pressure  motor_current  motor_rpm  \
0    0.349570      0.487848      0.029701       0.387062   0.419055   
1    0.478445      0.713509      0.029701       0.531396   0.647355   

   motor_temp  motor_vibe  type  
0    0.491978    0.208765     0  
1    0.716757    0.348482     0

In [590]:
g1_test = test_df[g1]
g2_test = test_df[g2]
g3_test = test_df[g3]
y_test = test_df[['type']]
combined_test = [g1_test, g2_test, g3_test]

svd = TruncatedSVD(n_components=1, n_iter=10, random_state=seed)
svd_list = []
for i in combined_test:
    result = svd.fit_transform(i)
    svd_list.append(result)
    total_var =svd.explained_variance_ratio_.sum() * 100
    print(f"{i}total_var : {total_var}")
    
flat_svd_list = []
for i in svd_list:
    result = [j for sub in i for j in sub]
    flat_svd_list.append(result)
svd_test_df = pd.DataFrame({"PC1": flat_svd_list[0], "PC2": flat_svd_list[1], "PC3": flat_svd_list[2]})
svd_test_df = pd.concat([svd_test_df, y_test], axis=1)
svd_test_df.info()

      air_inflow  motor_current
0       0.349570       0.387062
1       0.478445       0.531396
2      -0.329171      -0.392040
3       0.083228       0.081769
4      -0.037055      -0.056520
...          ...            ...
7384    0.014495       0.002423
7385   -0.535371      -0.621765
7386   -0.466638      -0.549220
7387   -0.440863      -0.521260
7388   -0.346355      -0.408664

[7389 rows x 2 columns]total_var : 99.55080635654565
      air_end_temp  motor_rpm  motor_temp
0         0.487848   0.419055    0.491978
1         0.713509   0.647355    0.716757
2        -0.725652  -0.806787   -0.718468
3         0.012350  -0.060812    0.017876
4        -0.202949  -0.278934   -0.197860
...            ...        ...         ...
7384     -0.110842  -0.185868   -0.104848
7385     -1.083715  -1.168869   -1.076305
7386     -0.970885  -1.053991   -0.962624
7387     -0.927134  -1.010367   -0.918702
7388     -0.752132  -0.832962   -0.744304

[7389 rows x 3 columns]total_var : 99.22881044537637
    

In [591]:
# svd= TruncatedSVD(n_components=3, n_iter=10, random_state=seed)
# svd_test_df = svd.fit_transform(X_test)
# svd_test_df = pd.DataFrame({"PC1": svd_test_df.T[0], "PC2": svd_test_df.T[1], "PC3": svd_test_df.T[2]})
# svd_test_df = pd.concat([svd_test_df, y_test], axis=1)
# svd_test_df

In [592]:
tdf0_test = svd_test_df[svd_test_df.type == 0]
tdf1_test = svd_test_df[svd_test_df.type == 1]
tdf2_test = svd_test_df[svd_test_df.type == 2]
tdf3_test = svd_test_df[svd_test_df.type == 3]
tdf4_test = svd_test_df[svd_test_df.type == 4]
tdf5_test = svd_test_df[svd_test_df.type == 5]
tdf6_test = svd_test_df[svd_test_df.type == 6]
tdf7_test = svd_test_df[svd_test_df.type == 7]
tdf_test = [tdf0_test, tdf1_test, tdf2_test, tdf3_test, tdf4_test, tdf5_test, tdf6_test, tdf7_test]

In [593]:
clusters = []
sil_scores = []

for i, tdf in enumerate(tdf_test):
    X_test = tdf.iloc[:,:-1]
    y_test = tdf[['type']]
    
    dbscan = DBSCAN(eps=best_eps[i], min_samples=best_min_samples[i]).fit(X_test)

    try: 
        sil_score = ss(X_test, dbscan.labels_)
        sil_scores.append(sil_score) 
    except:
        sil_scores.append("값없음") 
        
    clusters.extend(dbscan.labels_)

In [594]:
print(f"그룹별 Silhouette Score: {sil_scores}")

그룹별 Silhouette Score: [0.010692635325020365, '값없음', -0.5703847180672742, 0.099856868707551, 0.8244814455464289, -0.7746449898203651, -0.6807657833607914, -0.042115144735116204]


In [595]:
svd_test_df['label'] = clusters
svd_test_df['label'].value_counts()

 0     7053
-1      215
 3       17
 4       11
 6       11
 7       11
 5       10
 1        9
 2        9
 11       7
 13       7
 8        6
 9        6
 12       3
 14       3
 15       3
 16       3
 17       3
 10       2
Name: label, dtype: int64

In [596]:
def 결과정리(label):
    if label == 0: # 주된 다수 그룹만 정상(0), 나머지는 이상(1)
        return 0
    else:
        return 1

In [597]:
svd_test_df['label'] = svd_test_df['label'].apply(결과정리)
svd_test_df['label'].value_counts()

0    7053
1     336
Name: label, dtype: int64

In [598]:
overall_sil_score = ss(svd_test_df.iloc[:,:-2], svd_test_df['label'])
print(f"Silhouette Score: {overall_sil_score}")

Silhouette Score: 0.09912640077529473


In [599]:
fig = px.scatter_3d(
    svd_test_df, x='PC1', y='PC2', z='PC3', color='label',symbol='label', opacity=0.5, size_max=10,height=800,
    title = "1st DBSCAN Clustering"
)
fig.show()

In [600]:
fig = px.scatter_3d(
    svd_test_df[svd_test_df["label"] == 0], x='PC1', y='PC2', z='PC3', color='label',symbol='label', opacity=0.5, size_max=10,height=800,
    title = "Label 0(정상) Only"
)
fig.show()

In [601]:
X = svd_test_df.iloc[:,:-1]
gm_labels = gm.predict(X)
gm_proba = gm.predict_proba(X)
gm_new_probas = []
for i in gm_proba:
    k = np.around(i.astype(np.double), 6)
    gm_new_probas.append(k)
gm_new_probas

[array([0.000e+00, 9.971e-01, 0.000e+00, 2.897e-03, 0.000e+00, 0.000e+00,
        0.000e+00, 0.000e+00, 0.000e+00, 0.000e+00, 0.000e+00, 0.000e+00,
        0.000e+00, 0.000e+00, 0.000e+00, 0.000e+00, 0.000e+00, 3.000e-06,
        0.000e+00, 0.000e+00]),
 array([0.00000e+00, 9.99988e-01, 0.00000e+00, 9.00000e-06, 0.00000e+00,
        0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00,
        0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00, 0.00000e+00,
        0.00000e+00, 0.00000e+00, 2.00000e-06, 0.00000e+00, 0.00000e+00]),
 array([0.      , 0.      , 0.      , 0.545765, 0.      , 0.      ,
        0.      , 0.454235, 0.      , 0.      , 0.      , 0.      ,
        0.      , 0.      , 0.      , 0.      , 0.      , 0.      ,
        0.      , 0.      ]),
 array([0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0.]),
 array([0.00000e+00, 0.00000e+00, 0.00000e+00, 9.99996e-01, 0.00000e+00,
        0.00000e+00, 0.00000e+00, 4.00000e-06, 

In [602]:
svd_test_df['gm_label'] = gm_labels
svd_test_df['gm_proba'] = gm_new_probas
svd_test_df['gm_label'].value_counts()

7     758
3     723
2     472
12    457
10    443
8     405
0     405
15    403
11    393
13    384
14    378
17    373
18    321
9     308
19    253
4     252
1     241
6     236
16    177
5       7
Name: gm_label, dtype: int64

In [603]:
svd_test_df.head()

PC1       PC2       PC3  type  label  gm_label  \
0  0.520877 -0.807738  0.126617     0      0         1   
1  0.714065 -1.199604  0.225412     0      0         1   
2 -0.509973  1.299447 -0.389315     0      0         3   
3  0.116671  0.017558 -0.070974     0      0         3   
4 -0.066167  0.392344 -0.169769     0      0         3   

                                            gm_proba  
0  [0.0, 0.9971, 0.0, 0.002897, 0.0, 0.0, 0.0, 0....  
1  [0.0, 0.999988, 0.0, 9e-06, 0.0, 0.0, 0.0, 0.0...  
2  [0.0, 0.0, 0.0, 0.545765, 0.0, 0.0, 0.0, 0.454...  
3  [0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
4  [0.0, 0.0, 0.0, 0.999996, 0.0, 0.0, 0.0, 4e-06...

# DBSCAN 2nd Turn

In [604]:
svd_test_df = svd_test_df.reset_index(inplace=False)

In [605]:
test_df = svd_test_df[svd_test_df["label"] == 0]
test_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7053 entries, 0 to 7388
Data columns (total 8 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   index     7053 non-null   int64  
 1   PC1       7053 non-null   float64
 2   PC2       7053 non-null   float64
 3   PC3       7053 non-null   float64
 4   type      7053 non-null   int64  
 5   label     7053 non-null   int64  
 6   gm_label  7053 non-null   int64  
 7   gm_proba  7053 non-null   object 
dtypes: float64(3), int64(4), object(1)
memory usage: 495.9+ KB


In [606]:
X_test = test_df.iloc[:,1:4]
X_test.head(3)

PC1       PC2       PC3
0  0.520877 -0.807738  0.126617
1  0.714065 -1.199604  0.225412
2 -0.509973  1.299447 -0.389315

In [607]:
y_test = test_df[['index','type', 'label', 'gm_label', 'gm_proba']]
y_test.head(3)

index  type  label  gm_label  \
0      0     0      0         1   
1      1     0      0         1   
2      2     0      0         3   

                                            gm_proba  
0  [0.0, 0.9971, 0.0, 0.002897, 0.0, 0.0, 0.0, 0....  
1  [0.0, 0.999988, 0.0, 9e-06, 0.0, 0.0, 0.0, 0.0...  
2  [0.0, 0.0, 0.0, 0.545765, 0.0, 0.0, 0.0, 0.454...

In [608]:
eps = 0.05
min_sample = 3

In [609]:
dbscan = DBSCAN(eps=eps, min_samples=min_sample)
dbscan.fit_predict(X_test)

array([0, 0, 0, ..., 0, 0, 0], dtype=int64)

In [610]:
test_df  = pd.concat([X_test, y_test], axis=1)
test_df['label'] = dbscan.labels_
test_df.head(3)

PC1       PC2       PC3  index  type  label  gm_label  \
0  0.520877 -0.807738  0.126617      0     0      0         1   
1  0.714065 -1.199604  0.225412      1     0      0         1   
2 -0.509973  1.299447 -0.389315      2     0      0         3   

                                            gm_proba  
0  [0.0, 0.9971, 0.0, 0.002897, 0.0, 0.0, 0.0, 0....  
1  [0.0, 0.999988, 0.0, 9e-06, 0.0, 0.0, 0.0, 0.0...  
2  [0.0, 0.0, 0.0, 0.545765, 0.0, 0.0, 0.0, 0.454...

In [611]:
test_df['label'].value_counts()

 0     3975
 1     1107
 2     1076
 3       30
 19      27
 23      27
 36      26
 9       25
 31      24
 8       23
 10      22
 12      22
 24      22
 21      22
 46      22
 29      21
 6       21
 27      21
 33      21
 16      21
 17      20
 35      20
 34      20
 15      19
 14      19
 42      18
 13      18
 7       18
 41      17
 38      17
 11      17
 37      17
 30      17
 5       17
 4       17
 47      16
 50      16
 32      16
 22      16
 26      15
 39      15
 20      15
 45      15
 49      15
 28      14
 40      13
 43      13
 25      12
 44      11
 18      10
 48      10
-1        5
Name: label, dtype: int64

In [612]:
def 결과정리2(label):
    if label == -1: 
        return 1
    else:
        return 0

In [613]:
test_df['label'] = test_df['label'].apply(결과정리2).astype('int64')
test_df['label'].value_counts()

0    7048
1       5
Name: label, dtype: int64

In [614]:
fig = px.scatter_3d(
    test_df, x='PC1', y='PC2', z='PC3', color='label',symbol='label', opacity=0.5, size_max=10,height=800,
    title = "Additional Outliers"
)
fig.show()

In [615]:
svd_test_df = pd.merge(svd_test_df, test_df, how='left', on='index')
svd_test_df.head(3)

index     PC1_x     PC2_x     PC3_x  type_x  label_x  gm_label_x  \
0      0  0.520877 -0.807738  0.126617       0        0           1   
1      1  0.714065 -1.199604  0.225412       0        0           1   
2      2 -0.509973  1.299447 -0.389315       0        0           3   

                                          gm_proba_x     PC1_y     PC2_y  \
0  [0.0, 0.9971, 0.0, 0.002897, 0.0, 0.0, 0.0, 0....  0.520877 -0.807738   
1  [0.0, 0.999988, 0.0, 9e-06, 0.0, 0.0, 0.0, 0.0...  0.714065 -1.199604   
2  [0.0, 0.0, 0.0, 0.545765, 0.0, 0.0, 0.0, 0.454... -0.509973  1.299447   

      PC3_y  type_y  label_y  gm_label_y  \
0  0.126617     0.0      0.0         1.0   
1  0.225412     0.0      0.0         1.0   
2 -0.389315     0.0      0.0         3.0   

                                          gm_proba_y  
0  [0.0, 0.9971, 0.0, 0.002897, 0.0, 0.0, 0.0, 0....  
1  [0.0, 0.999988, 0.0, 9e-06, 0.0, 0.0, 0.0, 0.0...  
2  [0.0, 0.0, 0.0, 0.545765, 0.0, 0.0, 0.0, 0.454...

In [616]:
submit_df = svd_test_df[['type_x', 'label_x', 'label_y']]
submit_df['label_y'] = submit_df['label_y'].fillna(0)
submit_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7389 entries, 0 to 7388
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   type_x   7389 non-null   int64  
 1   label_x  7389 non-null   int64  
 2   label_y  7389 non-null   float64
dtypes: float64(1), int64(2)
memory usage: 230.9 KB


In [617]:
submit_df['label'] = submit_df['label_x'] + submit_df['label_y']  # 둘 중 하나라도 1(이상)이면 1(이상)이 되게...
submit_df.drop(['label_x', 'label_y'], axis=1, inplace=True)
submit_df.rename(columns = {'type_x' : 'type'}, inplace = True)
submit_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7389 entries, 0 to 7388
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   type    7389 non-null   int64  
 1   label   7389 non-null   float64
dtypes: float64(1), int64(1)
memory usage: 173.2 KB


In [618]:
submit_df["gm_label"] = svd_test_df["gm_label_x"]

In [619]:
submit_df['label'].value_counts()

0.0    7048
1.0     341
Name: label, dtype: int64

In [620]:
submit_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7389 entries, 0 to 7388
Data columns (total 3 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   type      7389 non-null   int64  
 1   label     7389 non-null   float64
 2   gm_label  7389 non-null   int64  
dtypes: float64(1), int64(2)
memory usage: 230.9 KB


In [621]:
fin_X = svd_test_df[['PC1_x', 'PC2_x', 'PC3_x']]
fin_y = submit_df['label']

overall_sil_score = ss(fin_X, fin_y)
print(f"Silhouette Score: {overall_sil_score}")

Silhouette Score: 0.09912958897545326


In [622]:
submit_df.to_csv('./submits/submit_20230412_05.csv', index=False)

In [623]:
# test_result = submit_df.groupby(['type', 'gm_label_y'])['label'].count().reset_index()
# test_result.to_csv('test1.csv', encoding="utf-8-sig")

KeyError: 'gm_label_y'